# RomKorr – Map Builder (v4)

Fixes ggü. v3:
- JS-Init wartet robust auf `window.L` und `map` → Linien/Filter werden sicher initialisiert.
- Linien werden in ein echtes **Folium-FeatureGroup** gezeichnet → erscheinen in der LayerControl.
- Heatmap blockt keine Klicks: `pointer-events: none`.
- „Alle Korrespondenzen“ pro Ort: Sidebar-Liste + Pagination + CSV.

Output: `outputs/romkorr_map.html`


In [7]:
from __future__ import annotations

from pathlib import Path
import json
import numpy as np
import pandas as pd

import folium
from folium.plugins import HeatMap, MarkerCluster
from branca.element import MacroElement, Template

In [8]:
PROJECT_ROOT = Path.cwd()

MASTER = PROJECT_ROOT / "data" / "processed" / "letters_master.parquet"
PLACES = PROJECT_ROOT / "data" / "processed" / "places_agg.parquet"

OUT_DIR = PROJECT_ROOT / "outputs"
OUT_DIR.mkdir(parents=True, exist_ok=True)
OUT_HTML = OUT_DIR / "romkorr_map.html"

CENTER = (51.0, 10.0)
ZOOM_START = 6

SAMPLE_FRAC_LINES = 1.0
TOP_N_PERSONS = 80
EXAMPLES_PER_PLACE = 6
PAGE_SIZE_PLACE_LIST = 50
COORD_ROUND = 5

In [9]:
letters = pd.read_parquet(MASTER)
places = pd.read_parquet(PLACES)

letters.shape, places.shape

((4388, 17), (277, 5))

In [10]:
def to_de_date(date_iso: str) -> str:
    if not isinstance(date_iso, str) or not date_iso:
        return "?"
    try:
        y, m, d = date_iso.split("-")
        return f"{d}.{m}.{y}"
    except Exception:
        return "?"

def coord_key(lat: float, lon: float, ndigits: int = COORD_ROUND) -> str:
    return f"{round(float(lat), ndigits)}|{round(float(lon), ndigits)}"

pc = pd.concat([letters["Sender"], letters["Recipient"]], ignore_index=True).fillna("Unknown")
pc = pc[pc.ne("Unknown")]
top_persons = pc.value_counts().head(TOP_N_PERSONS)
persons_list = [{"name": k, "count": int(v)} for k, v in top_persons.items()]

In [11]:
m = folium.Map(location=CENTER, zoom_start=ZOOM_START, control_scale=True, prefer_canvas=True)

heat_points = places.groupby(["lat","lon"], as_index=False)["count"].sum()
heat_layer = folium.FeatureGroup(name="Heatmap", show=True)
HeatMap(heat_points[["lat","lon","count"]].values.tolist(), radius=18, blur=20, max_zoom=7).add_to(heat_layer)
heat_layer.add_to(m)

hotspots_layer = folium.FeatureGroup(name="Hotspots", show=True)
cluster = MarkerCluster(name="Hotspot-Cluster").add_to(hotspots_layer)
hotspots_layer.add_to(m)

lines_group = folium.FeatureGroup(name="Linien", show=True)
lines_group.add_to(m)

m

In [12]:
letters_work = letters.copy()
letters_work["date_de"] = letters_work["date_iso"].map(to_de_date)

place_index = {}
place_name_by_key = {}

def add_place_entries(lat_col: str, lon_col: str, place_col: str):
    sub = letters_work.dropna(subset=[lat_col, lon_col]).copy()
    sub["k"] = [coord_key(a, b) for a, b in zip(sub[lat_col], sub[lon_col])]
    sub = sub.sort_values(["date_iso"], na_position="last")
    for _, r in sub.iterrows():
        k = r["k"]
        place_index.setdefault(k, []).append({
            "s": str(r.get("Sender","?")),
            "r": str(r.get("Recipient","?")),
            "d": str(r.get("date_de","?")),
            "u": str(r.get("link_canonical","#")),
            "id": int(r.get("letter_id")) if pd.notnull(r.get("letter_id")) else None,
        })

add_place_entries("dispatch_lat", "dispatch_lon", "place_dispatch")
add_place_entries("destination_lat", "destination_lon", "place_destination")

tmp = places.copy()
tmp["k"] = [coord_key(a, b) for a, b in zip(tmp["lat"], tmp["lon"])]
for k, grp in tmp.groupby("k"):
    s = grp["place_mode"].dropna()
    place_name_by_key[k] = (s.mode().iloc[0] if len(s.mode()) else "Ort (unbekannt)")

for _, r in heat_points.sort_values("count", ascending=False).iterrows():
    k = coord_key(r["lat"], r["lon"])
    cnt = int(r["count"])
    place_name = place_name_by_key.get(k, "Ort (unbekannt)")
    entries = place_index.get(k, [])
    examples = entries[:EXAMPLES_PER_PLACE]

    ex_items = []
    for e in examples:
        ex_items.append(
            f"<li>{e['s']} → {e['r']}, {e['d']}, <a href='{e['u']}' target='_blank'>Original</a></li>"
        )

    popup_html = (
        "<div style='max-width: 420px;'>"
        + f"<h4 style='margin:0 0 6px 0;'>{place_name}</h4>"
        + f"<div><b>Korrespondenzen:</b> {cnt}</div>"
        + "<hr style='margin:8px 0;' />"
        + "<div style='display:flex; gap:8px; align-items:center; margin-bottom:8px;'>"
        + (
            "<button "
            + f"onclick='window.rkOpenPlace && window.rkOpenPlace(\"{k}\")' "
            + "style='padding:6px 10px;border:1px solid #ddd;"
            "border-radius:8px;background:#fff;cursor:pointer;'>"
            + "Alle Korrespondenzen</button>"
        )
        + "</div>"
        + "<div><b>Beispiele:</b></div>"
        + "<ul style='padding-left: 18px; margin: 6px 0;'>"
        + ("".join(ex_items) if ex_items else "<li>Keine Beispiele verfügbar.</li>")
        + "</ul>"
        + "</div>"
    )


    folium.CircleMarker(
        location=[float(r["lat"]), float(r["lon"])],
        radius=max(3, min(18, np.log1p(cnt) * 3.0)),
        fill=True,
        fill_opacity=0.7,
        popup=folium.Popup(popup_html, max_width=460),
    ).add_to(cluster)

In [13]:
lines_df = letters.dropna(subset=["dispatch_lat","dispatch_lon","destination_lat","destination_lon"]).copy()
if 0 < SAMPLE_FRAC_LINES < 1:
    rng = np.random.default_rng(42)
    lines_df = lines_df.loc[rng.random(len(lines_df)) < SAMPLE_FRAC_LINES].copy()

lines_df["date_de"] = lines_df["date_iso"].map(to_de_date)

lines_payload = [
    {
        "a": [float(r.dispatch_lat), float(r.dispatch_lon)],
        "b": [float(r.destination_lat), float(r.destination_lon)],
        "s": str(r.Sender),
        "r": str(r.Recipient),
        "d": str(r.date_de),
        "km": (float(r.distance_km) if pd.notnull(r.distance_km) else None),
        "u": str(r.link_canonical),
        "id": int(r.letter_id),
    }
    for r in lines_df.itertuples(index=False)
]

place_payload = {k: {"place": place_name_by_key.get(k, "Ort (unbekannt)"), "items": v}
                 for k, v in place_index.items()}

In [14]:
template = Template(r"""
{% macro html(this, kwargs) %}

<style>
  canvas.leaflet-heatmap-layer { pointer-events: none !important; }
  .rk-sidebar {
    position: absolute; top: 10px; left: 10px; z-index: 9999;
    background: rgba(255,255,255,0.94); padding: 10px 12px;
    border-radius: 12px; box-shadow: 0 2px 12px rgba(0,0,0,.18);
    width: 360px; font-family: system-ui, -apple-system, Segoe UI, Roboto, Arial, sans-serif;
  }
  .rk-title { margin: 0 0 8px 0; font-size: 14px; font-weight: 650; }
  .rk-row { display:flex; gap:8px; align-items:center; margin: 6px 0; }
  .rk-row select { width: 100%; padding: 6px; border-radius: 10px; border: 1px solid #ddd; }
  .rk-row button { padding: 6px 10px; border-radius: 10px; border: 1px solid #ddd; background: #fff; cursor:pointer; }
  .rk-row label { font-size: 12px; display:flex; gap:8px; align-items:center; }
  .rk-meta { font-size: 12px; opacity: .85; margin-top: 6px; line-height: 1.35; }
  .rk-divider { height:1px; background:#eee; margin: 10px 0; }

  .rk-place h4 { margin: 0 0 6px 0; font-size: 13px; }
  .rk-list { max-height: 240px; overflow:auto; border: 1px solid #eee; border-radius: 10px; padding: 6px; background: #fff; }
  .rk-list-item { font-size: 12px; padding: 6px; border-bottom: 1px solid #f2f2f2; }
  .rk-list-item:last-child { border-bottom: none; }
  .rk-pager { display:flex; justify-content: space-between; align-items:center; margin-top: 6px; }
  .rk-pager button { padding: 4px 8px; border-radius: 10px; border: 1px solid #ddd; background:#fff; cursor:pointer; font-size: 12px; }
  .rk-muted { opacity: .75; }
</style>

<div class="rk-sidebar">
  <div class="rk-title">RomKorr – Filter & Details</div>

  <div class="rk-row">
    <label><input type="checkbox" id="rkShowLines" checked /> Linien anzeigen</label>
  </div>

  <div class="rk-row">
    <select id="rkPerson">
      <option value="">(alle Personen)</option>
    </select>
    <button id="rkReset" title="Filter zurücksetzen">Reset</button>
  </div>

  <div class="rk-meta">
    Linien: <span id="rkLineCount">0</span> (von <span id="rkLineTotal">0</span>)<br/>
    Filter matcht Sender <i>oder</i> Empfänger.
  </div>

  <div class="rk-divider"></div>

  <div class="rk-place" id="rkPlaceBox" style="display:none;">
    <h4 id="rkPlaceTitle"></h4>
    <div class="rk-row" style="margin-top:0;">
      <button id="rkPlaceDownload">CSV Download</button>
      <div class="rk-muted" id="rkPlaceMeta"></div>
    </div>
    <div class="rk-list" id="rkPlaceList"></div>
    <div class="rk-pager">
      <button id="rkPrev">◀</button>
      <div class="rk-muted"><span id="rkPage"></span></div>
      <button id="rkNext">▶</button>
    </div>
  </div>

  <div class="rk-meta rk-muted" style="margin-top:10px;">
    Tipp: Hotspot → „Alle Korrespondenzen“ öffnet die Liste hier.
  </div>
</div>

<script>
(function() {
  const map = {{this._parent.get_name()}};
  const LINES = {{ this.lines_json }};
  const PERSONS = {{ this.persons_json }};
  const PLACES = {{ this.places_json }};
  const PAGE_SIZE = {{ this.page_size }};
  const LINES_GROUP = "{{ this.lines_group_name }}";

  function safeText(s) { return (s || "").toString(); }

  function waitForReady(cb) {
    const ok = (typeof window !== "undefined") && window.L && map;
    if (!ok) return setTimeout(() => waitForReady(cb), 50);
    map.whenReady(() => cb());
  }

  waitForReady(() => {
    const L = window.L;
    const linesHost = window[LINES_GROUP] || L.layerGroup().addTo(map);

    function popupHtml(x) {
      const km = (x.km === null || x.km === undefined) ? "?" : (Math.round(x.km * 10) / 10).toFixed(1);
      return `
        <div style="max-width: 360px;">
          <b>${safeText(x.s)}</b> → <b>${safeText(x.r)}</b><br/>
          ${safeText(x.d)} · Distanz: ${km} km<br/>
          <a href="${safeText(x.u)}" target="_blank">Original</a>
        </div>`;
    }

    function clearLines() { if (linesHost.clearLayers) linesHost.clearLayers(); }

    function drawLines() {
      const showLines = document.getElementById('rkShowLines').checked;
      const filterName = document.getElementById('rkPerson').value;

      clearLines();
      if (!showLines) {
        document.getElementById('rkLineCount').textContent = "0";
        return;
      }

      let shown = 0;
      for (let i=0; i<LINES.length; i++) {
        const x = LINES[i];
        if (filterName && x.s !== filterName && x.r !== filterName) continue;

        const line = L.polyline([x.a, x.b], { weight: 1, opacity: 0.35 });
        line.bindPopup(popupHtml(x), {maxWidth: 380});
        line.addTo(linesHost);
        shown++;
      }
      document.getElementById('rkLineCount').textContent = shown.toString();
    }

    // Populate persons dropdown
    const sel = document.getElementById('rkPerson');
    PERSONS.forEach(p => {
      const opt = document.createElement('option');
      opt.value = p.name;
      opt.textContent = `${p.name} (${p.count})`;
      sel.appendChild(opt);
    });
    document.getElementById('rkLineTotal').textContent = LINES.length.toString();

    // Place list
    let currentKey = null;
    let currentPage = 0;

    function renderPlace() {
      if (!currentKey || !PLACES[currentKey]) return;
      document.getElementById('rkPlaceBox').style.display = 'block';

      const place = PLACES[currentKey];
      const items = place.items || [];
      const total = items.length;

      document.getElementById('rkPlaceTitle').textContent = place.place || "Ort";
      document.getElementById('rkPlaceMeta').textContent = `${total} Einträge`;
      document.getElementById('rkPage').textContent = `Seite ${currentPage+1} / ${Math.max(1, Math.ceil(total / PAGE_SIZE))}`;

      const start = currentPage * PAGE_SIZE;
      const end = Math.min(total, start + PAGE_SIZE);

      const list = document.getElementById('rkPlaceList');
      list.innerHTML = '';
      for (let i=start; i<end; i++) {
        const x = items[i];
        const div = document.createElement('div');
        div.className = 'rk-list-item';
        div.innerHTML = `${safeText(x.s)} → ${safeText(x.r)}, ${safeText(x.d)}, <a href="${safeText(x.u)}" target="_blank">Original</a>`;
        list.appendChild(div);
      }
    }

    window.rkOpenPlace = (key) => { currentKey = key; currentPage = 0; renderPlace(); };

    document.getElementById('rkPrev').addEventListener('click', () => {
      if (!currentKey) return;
      if (currentPage > 0) currentPage--;
      renderPlace();
    });
    document.getElementById('rkNext').addEventListener('click', () => {
      if (!currentKey || !PLACES[currentKey]) return;
      const total = (PLACES[currentKey].items || []).length;
      const maxPage = Math.max(0, Math.ceil(total / PAGE_SIZE) - 1);
      if (currentPage < maxPage) currentPage++;
      renderPlace();
    });

    document.getElementById('rkPlaceDownload').addEventListener('click', () => {
      if (!currentKey || !PLACES[currentKey]) return;
      const items = PLACES[currentKey].items || [];
      const rows = [["Sender","Empfänger","Datum","URL"]];
      items.forEach(x => rows.push([x.s, x.r, x.d, x.u]));
      const csv = rows.map(r => r.map(v => `"${safeText(v).replaceAll('"','""')}"`).join(",")).join("\n");
      const blob = new Blob([csv], {type: "text/csv;charset=utf-8;"});
      const url = URL.createObjectURL(blob);
      const a = document.createElement("a");
      a.href = url;
      a.download = `romkorr_${(PLACES[currentKey].place || "ort").replaceAll(" ","_")}.csv`;
      document.body.appendChild(a); a.click(); document.body.removeChild(a);
      URL.revokeObjectURL(url);
    });

    // Events
    document.getElementById('rkShowLines').addEventListener('change', drawLines);
    sel.addEventListener('change', drawLines);
    document.getElementById('rkReset').addEventListener('click', () => {
      sel.value = "";
      document.getElementById('rkShowLines').checked = true;
      drawLines();
    });

    // Initial draw
    drawLines();
  });
})();
</script>

{% endmacro %}
""")

macro = MacroElement()
macro._template = template
macro.lines_json = json.dumps(lines_payload, ensure_ascii=False)
macro.persons_json = json.dumps(persons_list, ensure_ascii=False)
macro.places_json = json.dumps(place_payload, ensure_ascii=False)
macro.page_size = PAGE_SIZE_PLACE_LIST
macro.lines_group_name = lines_group.get_name()

m.get_root().add_child(macro)

In [15]:
folium.LayerControl().add_to(m)
m.save(str(OUT_HTML))
OUT_HTML

WindowsPath('g:/Meine Ablage/CodingProjekte/RomKorr/RomKorr/outputs/romkorr_map.html')